In [2]:
from joblib import load

from dask.distributed import Client
import odc.geo.xr
import pandas as pd
from dea_tools.spatial import subpixel_contours

from dep_coastlines.clean_rasters import Cleaner, calculate_consensus_land, remove_disconnected_land
from dep_coastlines.MosaicLoader import MultiyearMosaicLoader

In [3]:
cleaner = Cleaner()

In [8]:
loader = MultiyearMosaicLoader(start_year=1999, end_year=2023, version="0.6.0.4")

cell = (62, 30)
df = pd.DataFrame([cell])
df.index = [cell]
ds = loader.load(df)
ds

<xarray.Dataset>
Dimensions:          (x: 748, y: 953, year: 6)
Coordinates:
    band             int64 1
  * x                (x) float64 7.221e+05 7.222e+05 ... 7.445e+05 7.445e+05
  * y                (y) float64 -9.297e+05 -9.298e+05 ... -9.583e+05 -9.583e+05
    spatial_ref      int64 0
  * year             (year) <U4 '2017' '2018' '2019' '2020' '2021' '2022'
Data variables: (12/60)
    blue             (year, y, x) float32 dask.array<chunksize=(1, 953, 748), meta=np.ndarray>
    blue_mad         (year, y, x) float32 dask.array<chunksize=(1, 953, 748), meta=np.ndarray>
    count            (year, y, x) float32 dask.array<chunksize=(1, 953, 748), meta=np.ndarray>
    green            (year, y, x) float32 dask.array<chunksize=(1, 953, 748), meta=np.ndarray>
    green_mad        (year, y, x) float32 dask.array<chunksize=(1, 953, 748), meta=np.ndarray>
    nir08            (year, y, x) float32 dask.array<chunksize=(1, 953, 748), meta=np.ndarray>
    ...               ...
    mndwi_all        (y, x) float32 dask.array<chunksize=(953, 748), meta=np.ndarray>
    ndwi_all         (y, x) float32 dask.array<chunksize=(953, 748), meta=np.ndarray>
    nirwi_all        (y, x) float32 dask.array<chunksize=(953, 748), meta=np.ndarray>
    meanwi_all       (y, x) float32 dask.array<chunksize=(953, 748), meta=np.ndarray>
    wix_all          (y, x) float32 dask.array<chunksize=(953, 748), meta=np.ndarray>
    maxwi_all        (y, x) float32 dask.array<chunksize=(953, 748), meta=np.ndarray>

In [38]:
with Client():
    output = cleaner.model.apply_mask(ds)


predicting...
predicting...
predicting...
predicting...
predicting...
predicting...
predicting...
predicting...
predicting...
predicting...
predicting...
predicting...


/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/dask/core.py:127: RuntimeWarning: divide by zero encountered in divide
  return func(*(_execute_task(a, cache) for a in args))
/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/dask/core.py:127: RuntimeWarning: divide by zero encountered in divide
  return func(*(_execute_task(a, cache) for a in args))
/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/dask/core.py:127: RuntimeWarning: invalid value encountered in divide
  return func(*(_execute_task(a, cache) for a in args))
/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/dask/core.py:127: RuntimeWarning: divide by zero encountered in divide
  return func(*(_execute_task(a, cache) for a in args))
/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/dask/core.py:127: RuntimeWarning: invalid value encountered in divide
  return func(*(_execute_task(a, cache) for a in args

KeyError: "No variable named 0. Variables on the dataset include ['blue', 'blue_mad', 'count', 'green', 'green_mad', ..., 'band', 'x', 'y', 'spatial_ref', 'year']"

In [10]:
import folium
m = output.sel(year='2018').nir08.odc.explore(layer_control=False)
m = ds.sel(year='2018').nir08.odc.explore(map=m)
#folium.LayerControl().add_to(m) 
m


In [13]:
output.sel(year="2018").rio.to_raster('../masked6230.tif')

In [23]:
candidate_land = cleaner.land(output)
consensus_land = calculate_consensus_land(ds.isel(year=1)).compute()
connected_areas = remove_disconnected_land(consensus_land, candidate_land.compute())
connected_areas.astype(int).sel(year='2018').odc.explore()

In [24]:
import xrspatial as xs
no_connected_neighbors = xs.focal.mean(consensus_land) == 0
suspicious_connected_areas = candidate_land & no_connected_neighbors
analysis_zone = connected_areas & ~suspicious_connected_areas
analysis_zone.sel(year='2018').astype(int).odc.explore()

In [37]:
analysis_zone = cleaner.expand_analysis_zone(analysis_zone, output)
# analysis_zone.sel(year='2018').astype(int).rio.to_raster('../azone.tif')



predicting...
predicting...
predicting...
predicting...
predicting...
predicting...


/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/dask/core.py:127: RuntimeWarning: divide by zero encountered in divide
  return func(*(_execute_task(a, cache) for a in args))
/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/dask/core.py:127: RuntimeWarning: divide by zero encountered in divide
  return func(*(_execute_task(a, cache) for a in args))
/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/dask/core.py:127: RuntimeWarning: divide by zero encountered in divide
  return func(*(_execute_task(a, cache) for a in args))
/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/dask/core.py:127: RuntimeWarning: invalid value encountered in divide
  return func(*(_execute_task(a, cache) for a in args))
/home/jesse/Projects/D4D/dep-coastlines/venv/lib/python3.10/site-packages/dask/core.py:127: RuntimeWarning: invalid value encountered in divide
  return func(*(_execute_task(a, cache) for a in args

KeyError: "No variable named 0. Variables on the dataset include ['blue', 'blue_mad', 'count', 'green', 'green_mad', ..., 'band', 'x', 'y', 'spatial_ref', 'year']"

In [41]:
def water(xr):
    return output.meanwi >= 0

from odc.algo import mask_cleanup
from dep_coastlines.raster_cleaning import load_gadm_land, find_inland_areas
gadm_land = load_gadm_land(output)

land = gadm_land | consensus_land
ocean = mask_cleanup(~land, mask_filters=[("erosion", 2)])
inland_areas = find_inland_areas(water(output), ocean)
inland_areas.sel(year="2018").astype(int).odc.explore()

toutput = (
            output.meanwi
            .where(analysis_zone, 0.5)
            .where(~inland_areas)
        )

toutput.groupby("year").map(xs.focal.mean).sel(year='2018').odc.explore()

In [57]:

ocean = ~land
mask_cleanup(land, mask_filters=[("closing", 20)]).odc.explore()
# ocean.odc.explore()


In [58]:
cleaner.water(output.sel(year='2022')).odc.explore()

In [17]:
inland_areas = find_inland_areas(cleaner.water(output), ocean)
inland_areas.sel(year='2022').astype(int).odc.explore()

In [34]:
analysis_zone = analysis_zone | mask_cleanup(cleaner.land(output.where(analysis_zone)), mask_filters=[("dilation", 1)])
# output.ndwi.where(analysis_zone).sel(year='2022').odc.explore()

output.ndwi.where(analysis_zone, 0.5).rio.to_raster('../o5.tif')

In [35]:
combined_gdf = subpixel_contours(
    output.ndwi.where(analysis_zone, 0.5),
    dim="year",
    z_values=[cleaner.index_threshold],
    min_vertices=5,
)
combined_gdf.explore()

combined_gdf.to_file('c5.gpkg')

Loading data into memory using Dask
Operating in single z-value, multiple arrays mode


In [18]:
output = output['ndwi'].where(analysis_zone, 0.5).compute()
output.sel(year='2022').odc.explore()

In [20]:

#output = (
#    output[cleaner.water_index]
#    .where(analysis_zone, obvious_water)
#    .where(~inland_areas)
#)
#output = output.groupby("year").map(xs.focal.mean)
combined_gdf = subpixel_contours(
    output,
    dim="year",
    z_values=[cleaner.index_threshold],
    min_vertices=5,
)
combined_gdf.explore()

Operating in single z-value, multiple arrays mode
